<a href="https://colab.research.google.com/github/aman8533/Building-an-Optimized-algorithm-that-provides-summaries-of-legal-documents/blob/main/Motions.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
! pip install numpy
! pip install wandb
! pip install transformers
! pip install seaborn
! pip install PyPDF2
! pip install Sentencepiece
! pip install pdfplumber transformers
! pip install spacy
! pip install -U matplotlib
! pip install pytextrank
! pip install pandas
! pip install spacy python -m spacy download en_core_web_sm
!python -m spacy download en_core_web_sm
!python -m spacy download en_core_web_lg
import PIL.Image
if not hasattr(PIL.Image, 'Resampling'):  # Pillow<9.0
  PIL.Image.Resampling = PIL.Image
from transformers import pipeline

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in

In [ ]:
! pip install pytextrank
! pip install pandas
! pip install matplotlib
! pip install datasets

In [ ]:
# let's load in our data set as a pandas data frame

import numpy as np
import pandas as pd
#import cv2
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import string
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
# quiet future deprecation warnings
import warnings
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import cross_val_score
import torch
import transformers as ppb
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader, RandomSampler, SequentialSampler
# Importing the T5 modules from huggingface/transformers
from transformers import T5Tokenizer, T5ForConditionalGeneration
# WandB – Import the wandb library
import wandb
from transformers import BertModel
#from transformers import pipeline
import spacy
import pytextrank
warnings.filterwarnings('ignore')

from google.colab import drive
drive.mount('/content/drive')
%cd /content/drive/My Drive/Cases/

# Our data is stored on Google Cloud.
# We can use a command like this to upload it into Google Colab's file system
#!wget - q - -show - progress

#url='https://drive.google.com/file/d/0B6GhBwm5vaB2ekdlZW5WZnppb28/view?usp=sharing'
#url='https://drive.google.com/uc?id=' + url.split('/')[-2]

df = pd.read_csv("https://storage.googleapis.com/inspirit-ai-data-bucket-1/Data/AI%20%2B%20X/Group/Journalism/Clickbait/clickbait_data.csv")

clickbait_data = pd.read_csv("https://storage.googleapis.com/inspirit-ai-data-bucket-1/Data/AI%20%2B%20X/Group/Journalism/Clickbait/clickbait_data.csv")

# #pd.read_csv("clickbait_data.csv")

print(clickbait_data.head())
print(clickbait_data.sort_values("total_views"))
sns.histplot(clickbait_data['total_views'], bins=40)
print("Max views:", np.max(clickbait_data['total_views']))
print("Min views:", np.min(clickbait_data['total_views']))
max_views = np.max(clickbait_data['total_views'])
min_views = np.min(clickbait_data['total_views'])
print("Max views title:", clickbait_data[clickbait_data['total_views'] == max_views]["title"])
print("Min views title:", clickbait_data[clickbait_data['total_views'] == min_views]["title"])

# # another way
sorted_df = clickbait_data.sort_values(by="total_views")
print("Max views title:", sorted_df['title'].iloc[-1])
print("Min views title:", sorted_df['title'].iloc[0])
sorted_df.head(1)
sorted_df.tail(1)

# from collections import Counter

# stpwrds = stopwords.words('english')
# punctuation = string.punctuation

# # try changing to visualize more or less words
# num_words = 15

# # text cleaning maintaining all of our text as one string
# text = " ".join(clickbait_data['title'])
# # text = text.lower() # try adding this back in and see what happens!
# text = "".join(_ for _ in text if _ not in punctuation)
# text = [t for t in text.split() if t not in stpwrds and not t.isdigit()]

# # We can use Counter to find the most frequent words in all our titles!
# words = [_[0] for _ in Counter(text).most_common(num_words)]
# frequency = [_[1] for _ in Counter(text).most_common(num_words)]

# # Making our plot look nice!
# plt.figure(figsize=(8, 6));
# ax = sns.barplot(x=frequency, y=words)
# ax.spines['top'].set_visible(False)
# ax.spines['right'].set_visible(False)
# plt.title("Most Frequent Keywords used in 5 Minute Craft Video Titles");
# plt.xlabel("Frequency", fontsize=14);
# plt.yticks(fontsize=14);
# plt.xticks(fontsize=14);

# # something something correlated to likes
# from collections import Counter

# stpwrds = stopwords.words('english')
# punctuation = string.punctuation

# # text cleaning maintaining all of our text as one string
# text = " ".join(clickbait_data['title'])
# # text = text.lower() # try adding this back in and see what happens!
# text = "".join(_ for _ in text if _ not in punctuation)
# text = [t for t in text.split() if t not in stpwrds and not t.isdigit()]

# top100 = Counter(text).most_common(100)

# setting up code to get averages
# averages = []
# for t in top100:
#     t = t[0]
#     # this will give us a 1 in the row if the word is in the title, or a 0 otherwise
#     titles_where_word_appears = clickbait_data['title'].apply(lambda x: 1 if t in x else 0)
#     # if we multiply this by the number of views of the video, if the video contains the word we will count the views
#     total_views_for_word = clickbait_data['total_views'] * titles_where_word_appears
#     # making sure we don't divide by zero
#     if sum(titles_where_word_appears) == 0:
#         averages.append((t, 0))
#     else:
#         # taking the average!
#         averages.append((t, sum(total_views_for_word) / sum(titles_where_word_appears)))

# # sorting our list of words and averages so we can see the top ones
# averages.sort(key=lambda x: x[1], reverse=True)

# # creating plot! We're plotting the words in the top 20 for average views
# plt.figure(figsize=(10, 6));
# ax = sns.barplot(x=[a[1] for a in averages[:20]], y=[a[0] for a in averages[:20]])

# # cosmetic graph edits
# ax.spines['top'].set_visible(False)
# ax.spines['right'].set_visible(False)
# plt.title("Keywords linked with higher number of views");
# plt.xlabel("Average Views", fontsize=14);
# plt.yticks(fontsize=14);
# plt.xticks(fontsize=14);
# plt.ticklabel_format(style='plain', axis='x', useOffset=False)

X_train, X_test, y_train, y_test = train_test_split(clickbait_data["title"], clickbait_data["total_views"],
                                                     test_size=0.2, random_state=9)
print(X_train.shape)
print(y_train.shape)
print(X_test.shape)
print(y_test.shape)

import nltk
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize

nltk.download('omw-1.4')

nltk.download('stopwords')
nltk.download('wordnet')
nltk.download('punkt')



def process_lang_data(text):
    '''
      For a given text, go through the process of tokenizing, removing stopwords,
      stemming / lemmatization, and removing punctuation. Return the cleaned text.
    '''
    cleaned_text = []
    punctuation = string.punctuation
    our_stopwords = stopwords.words('english')
    lemmatizer = WordNetLemmatizer()

    for token in word_tokenize(text):
        if token not in punctuation and token not in our_stopwords:
            clipped_token = lemmatizer.lemmatize(token)
            cleaned_text.append(clipped_token)

    return cleaned_text


from sklearn.feature_extraction.text import CountVectorizer

bow = CountVectorizer(analyzer=process_lang_data, max_features=1000)  # using the function we made above
bow.fit(X_train)  # fitting to our training data
bow_train = bow.transform(X_train).toarray()  # then transforming both training and testing data
bow_test = bow.transform(X_test).toarray()

import gensim

# have to pre-tokenize
tokenize = clickbait_data['title'].apply(process_lang_data)

# take a look at the documentation to see what these parameters are changing!
w2vec_model = gensim.models.Word2Vec(tokenize, min_count=1, size=10, window=5, sg=1)
w2vec_model.train(tokenize, total_examples=len(clickbait_data['title']), epochs=20)

#vectors = np.asarray(w2vec_model.wv.vectors)
#labels = np.asarray(w2vec_model.wv.index_to_key)  # fixed-width numpy strings

#x_vals = [v[0] for v in vectors]
#y_vals = [v[1] for v in vectors]
#print ("X Value = ", x_vals, "Y Value= ", y_vals)
#print ("Labels = ", labels)

import PyPDF2

# creating a pdf file object
pdfFileObj = open('SupremeCourtCase1.PDF', 'rb')

# creating a pdf reader object
pdfReader = PyPDF2.PdfFileReader(pdfFileObj)

# printing number of pages in pdf file
print(pdfReader.numPages)

# creating a page object
pageObj = pdfReader.getPage(0)

# extracting text from page
print(pageObj.extractText())

docList= ["SupremeCourtCase1.PDF","SupremeCourtCase2.PDF","SupremeCourtCase3.PDF","SupremeCourtCase4.PDF",
          "SupremeCourtCase5.PDF","SupremeCourtCase6.PDF","SupremeCourtCase7.PDF","SupremeCourtCase8.PDF",
          "SupremeCourtCase9.PDF","SupremeCourtCase10.PDF","SupremeCourtCase11.PDF","SupremeCourtCase12.PDF"]
document=[]

for cases in docList:
  pdfFileObj = open(cases, 'rb')
  pdfReader = PyPDF2.PdfFileReader(pdfFileObj)
  documentPage = []
  for page in range(pdfReader.numPages):
        pageObj = pdfReader.getPage(page)
        strCleanData = pageObj.extractText() #process_lang_data(pageObj.extractText())
        documentPage.append(strCleanData)
  document.append(documentPage)
  pdfFileObj.close()
print ("Cleaned Case File ", document)
bow = CountVectorizer(analyzer=process_lang_data, max_features=1000)  # using the function we made above

X_train, X_test, y_train, y_test = train_test_split(document[0][0],document[0][0],
                                                    test_size=0.2, random_state=9)


model_class, tokenizer_class, pretrained_weights = (ppb.DistilBertModel, ppb.DistilBertTokenizer, 'distilbert-base-uncased')
tokenizer = tokenizer_class.from_pretrained(pretrained_weights)
model = model_class.from_pretrained(pretrained_weights)

print(tokenizer)
#tokenized = document[0][0].apply((lambda x: tokenizer.encode(x, add_special_tokens=True)))
print("Case 1 = ",document)
print ("X_train = ",X_train)
print ("X_test = ",X_test)
print ("y_train = ",y_train)
print ("y_test = ",y_test)

#model = BertModel.from_pretrained("bert-base-cased")
#model.save_pretrained("directory_on_my_computer")

#sequences = ["Hello!", "Cool.", "Nice!"]

#encoded_sequences = [
#    [101, 7592, 999, 102],
#    [101, 4658, 1012, 102],
#    [101, 3835, 999, 102],
#]

#import torch

#model_inputs = torch.tensor(encoded_sequences)

#output = model(model_inputs)


## Want BERT instead of distilBERT? Uncomment the following line:
#model_class, tokenizer_class, pretrained_weights = (ppb.BertModel, ppb.BertTokenizer, 'bert-base-uncased')

# How to retrieve training data  and train it ?
# bow.fit(X_train)  # fitting to our training data
# bow_train = bow.transform(X_train).toarray()  # then transforming both training and testing data
# bow_test = bow.transform(X_test).toarray()

# print ("Bow Train", bow_train)
# print ("Bow Test", bow_test)
# # closing the pdf file object

# from transformers import BartTokenizer, BartForConditionalGeneration, BartConfig

# model = BartForConditionalGeneration.from_pretrained('sshleifer/distilbart-cnn-12-6')
# tokenizer = BartTokenizer.from_pretrained('sshleifer/distilbart-cnn-12-6')

#extracted_text1 = document[0][10]
#inputs = tokenizer([extracted_text1], truncation=True, return_tensors='pt')
# Generate Summary
#summary_ids = model.generate(inputs['input_ids'], num_beams=4, early_stopping=True, min_length=0, max_length=1024)
#summarized_text1 = ([tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=True) for g in summary_ids])
#print ("Extracted Text is",extracted_text1 )
#print("Summary Page 0 is:",summarized_text1)

#extracted_text2 = document[0][15]
#inputs = tokenizer([extracted_text2], truncation=True, return_tensors='pt')
# Generate Summary
#summary_ids = model.generate(inputs['input_ids'], num_beams=4, early_stopping=True, min_length=0, max_length=1024)
#summarized_text2 = ([tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=True) for g in summary_ids])
#print ("Extracted Text is",extracted_text2 )
#print("Summary Page 1 is:",summarized_text2)

#extracted_text3 = document[0][25]
#inputs = tokenizer([extracted_text3], truncation=True, return_tensors='pt')
# Generate Summary
#summary_ids = model.generate(inputs['input_ids'], num_beams=4, early_stopping=True, min_length=0, max_length=1024)
#summarized_text3 = ([tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=True) for g in summary_ids])
#print ("Extracted Text is",extracted_text3 )
#print("Summary Page 2 is:",summarized_text3)


#extracted_text4 = document[0][30]
#inputs = tokenizer([extracted_text4], truncation=True, return_tensors='pt')
# Generate Summary
#summary_ids = model.generate(inputs['input_ids'], num_beams=4, early_stopping=True, min_length=0, max_length=1024)
#summarized_text4 = ([tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=True) for g in summary_ids])
#print ("Extracted Text is",extracted_text )
#print("Summary Page 2 is:",summarized_text4)

# import pdfplumber

# document=[]
# iIndex = 0
# for cases in docList:
#   documentPage = []
#   extracted_text = ""
#   with pdfplumber.open(cases) as pdf:
#     totalpages = len(pdf.pages)
#     for i in range(0,totalpages):
#       extracted_page = pdf.pages[i]
#       extracted_text = extracted_page.extract_text()
#       documentPage.append(extracted_text)
#   document.append(documentPage)
#   #print ("Extracted Text", iIndex, " is: ", extracted_text)
#   #document.append(extracted_text)
#   iIndex+=1
#   pdf.close()


#iIndexDoc = 0
#for documentObj in document:
#  extracted_text = document[iIndexDoc]
#  inputs = tokenizer([extracted_text], truncation=True, return_tensors='pt')
#  summary_ids = model.generate(inputs['input_ids'], num_beams=4, early_stopping=True, min_length=0, max_length=30000)
#  summarized_text = ([tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=True) for g in summary_ids])
#  print ("Summarized Text of Doc ", iIndexDoc, " Is :", summarized_text)
#  iIndexDoc+=1

# iIndexDoc = 0
# for documentObj in document:
#   jPages = 0
#   summarized_text = []
#   for pagesObj in documentObj:
#     extracted_text = document[iIndexDoc][jPages]
#     inputs = tokenizer([extracted_text], truncation=True, return_tensors='pt')
#     summary_ids = model.generate(inputs['input_ids'], num_beams=4, early_stopping=True, min_length=0, max_length=1024)
#     tempsummarized_text = ([tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=True) for g in summary_ids])
#     summarized_text.append(tempsummarized_text)
#     jPages+=1
#   print ("Summarized Text of Document ", iIndexDoc, " is ",summarized_text)
#   iIndexDoc+=1

nlp = spacy.load("en_core_web_lg")
nlp.add_pipe("textrank")

doc = nlp(document[0][1])

for sent in doc._.textrank.summary(limit_phrases=2, limit_sentences=2):
      print(sent)

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


Mounted at /content/drive
/content/drive/My Drive/Cases
        video_id                                              title  \
0  v=XHTofu5wbbM  SUPER LAZY LIFE HACKS || Cool Hacks To Make Yo...   
1  v=HGxx0umIQvk  YUM! EASY SMART FOOD HACKS || Tasty Recipes Fo...   
2  v=Tt4RMk3Ih04                  HELPFUL LIFE HACKS FOR YOUR HOUSE   
3  v=A2MTydM5e58  USEFUL HACKS FOR YOUR HOME || Simple Tips That...   
4  v=_halJ4yrmGQ  ARE YOU A CRAFTY MOM? Amazing Parenting Hacks ...   

   active_since_days  duration_seconds  total_views  num_chars  num_words  \
0                 22               623       295614         60         12   
1                  1               739       130544         87         17   
2                  1               960        17834         33          6   
3                 30               833      3128867         66         12   
4                 15              3600      4210362         56         10   

   num_punctuation  num_words_uppercase  num_words_low

[nltk_data] Downloading package omw-1.4 to /root/nltk_data...
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


91
Supreme Court of tbe Wniteb States 
STATE OF SOUTH CAROLINA, 
Plaintiff, 
v. 
STATE OF NORTH CAROLINA, 
Defendant. 
On Motion for Leave To File Complaint MOTION OF THE STATE OF SOUTH CAROLINA FOR LEAVE TO FILE COMPLAINT, COMPLAINT, 
AND BRIEF IN SUPPORT OF ITS MOTION FOR LEAVE TO FILE COMPLAINT 
DAVID C. FREDERICK 
SCOTT H. ANGSTREICH 
KELLOGG, HUBER, HANSEN, 
TODD, EVANS & FIGEL, 
P.L.L.C. 1615 
M Street, N.W. 
Suite 400 Washington, 
D.C. 20036 (202) 326-7900 
Special Counsel to the State of South Carolina 
June 7,2007 HENRY DARGAN MCMASTER 
Attorney General 
JOHN W. MCINTOSH 
Chief Deputy Attorney General 
ROBERT D. COOK 
Assistant Deputy Attorney General Counsel of Record 
T. PARKIN HUNTER 
Assistant Attorney General 
LEIGH CHILDS CANTEY 
Assistant Attorney General 
Post Office Box 11549 Columbia, SC 2921 
1 
(803) 734-3970 
Cot~nsel for the State of South Carolina 


Cleaned Case File  [['Supreme Court of tbe Wniteb States \nSTATE OF SOUTH CAROLINA, \nPlaintiff, \nv. \nSTATE OF NORTH CAROLINA, \nDefendant. \nOn Motion for Leave To File Complaint MOTION OF THE STATE OF SOUTH CAROLINA FOR LEAVE TO FILE COMPLAINT, COMPLAINT, \nAND BRIEF IN SUPPORT OF ITS MOTION FOR LEAVE TO FILE COMPLAINT \nDAVID C. FREDERICK \nSCOTT H. ANGSTREICH \nKELLOGG, HUBER, HANSEN, \nTODD, EVANS & FIGEL, \nP.L.L.C. 1615 \nM Street, N.W. \nSuite 400 Washington, \nD.C. 20036 (202) 326-7900 \nSpecial Counsel to the State of South Carolina \nJune 7,2007 HENRY DARGAN MCMASTER \nAttorney General \nJOHN W. MCINTOSH \nChief Deputy Attorney General \nROBERT D. COOK \nAssistant Deputy Attorney General Counsel of Record \nT. PARKIN HUNTER \nAssistant Attorney General \nLEIGH CHILDS CANTEY \nAssistant Attorney General \nPost Office Box 11549 Columbia, SC 2921 \n1 \n(803) 734-3970 \nCot~nsel for the State of South Carolina ', 'TABLE OF CONTENTS MOTION FOR LEAVE TO FILE COMPLAINT COMPLAINT 

Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertModel: ['vocab_projector.bias', 'vocab_projector.weight', 'vocab_layer_norm.bias', 'vocab_transform.bias', 'vocab_layer_norm.weight', 'vocab_transform.weight']
- This IS expected if you are initializing DistilBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


PreTrainedTokenizer(name_or_path='distilbert-base-uncased', vocab_size=30522, model_max_len=512, is_fast=False, padding_side='right', truncation_side='right', special_tokens={'unk_token': '[UNK]', 'sep_token': '[SEP]', 'pad_token': '[PAD]', 'cls_token': '[CLS]', 'mask_token': '[MASK]'})
Case 1 =  [['Supreme Court of tbe Wniteb States \nSTATE OF SOUTH CAROLINA, \nPlaintiff, \nv. \nSTATE OF NORTH CAROLINA, \nDefendant. \nOn Motion for Leave To File Complaint MOTION OF THE STATE OF SOUTH CAROLINA FOR LEAVE TO FILE COMPLAINT, COMPLAINT, \nAND BRIEF IN SUPPORT OF ITS MOTION FOR LEAVE TO FILE COMPLAINT \nDAVID C. FREDERICK \nSCOTT H. ANGSTREICH \nKELLOGG, HUBER, HANSEN, \nTODD, EVANS & FIGEL, \nP.L.L.C. 1615 \nM Street, N.W. \nSuite 400 Washington, \nD.C. 20036 (202) 326-7900 \nSpecial Counsel to the State of South Carolina \nJune 7,2007 HENRY DARGAN MCMASTER \nAttorney General \nJOHN W. MCINTOSH \nChief Deputy Attorney General \nROBERT D. COOK \nAssistant Deputy Attorney General Counsel of 

ImportError: ignored

<Figure size 432x288 with 1 Axes>

In [ ]:
nlp = spacy.load("en_core_web_lg")
nlp.add_pipe("textrank")

doc = nlp(document[0][0])

for sent in doc._.textrank.summary(limit_phrases=2, limit_sentences=2):
      print(sent)

phrases_and_ranks = [ 
    (phrase.chunks[0], phrase.rank) for phrase in doc._.phrases
]
phrases_and_ranks[:10]

In [ ]:
!pip3 install torch==1.5.0

In [ ]:
!pip install pytorch-transformers

In [ ]:
!pip install rouge
from transformers import pipeline
import os
import torch
import torch.nn as nn
import spacy
import pytextrank
from transformers import T5Tokenizer, T5ForConditionalGeneration
from transformers import PegasusForConditionalGeneration
from transformers import PegasusTokenizer
from transformers import BertTokenizer, BertModel
from transformers import DistilBertModel, DistilBertTokenizer
import torch
from rouge import Rouge

#Summarization of text. Potential models that I will use are: TextRank, LexRank, Latent Semantic 
#Analysis, T5 transformers, BART transformers, GPT-2 Transformers, XLM Transformers. PEGASUS,

os.environ["CUDA_VISIBLE_DEVICES"] = "0"

# Text Rank Module Start - Extractive Summary
text = """One month after the United States began what has become a troubled rollout of a national COVID vaccination campaign, the effort is finally gathering real steam.
Close to a million doses -- over 951,000, to be more exact -- made their way into the arms of Americans in the past 24 hours, the U.S. Centers for Disease Control and Prevention reported Wednesday. That's the largest number of shots given in one day since the rollout began and a big jump from the previous day, when just under 340,000 doses were given, CBS News reported.
That number is likely to jump quickly after the federal government on Tuesday gave states the OK to vaccinate anyone over 65 and said it would release all the doses of vaccine it has available for distribution. Meanwhile, a number of states have now opened mass vaccination sites in an effort to get larger numbers of people inoculated, CBS News reported."""
nlp = spacy.load("en_core_web_lg")
nlp.add_pipe("textrank")
doc = nlp(text)
for sent in doc._.textrank.summary(limit_phrases=2, limit_sentences=2):
      print(sent)
Phrases_and_ranks = [(phrase.chunks[0], phrase.rank) for phrase in doc._.phrases]
Phrases_and_ranks[:10]
print ("Text Rank: ", Phrases_and_ranks)
# Text Rank Module End

# T5 Model Start - Abstraction Encoding/Decoding
summarizer = pipeline("summarization", model="t5-base", tokenizer="t5-base", framework="tf")
text = """One month after the United States began what has become a troubled rollout of a national COVID vaccination campaign, the effort is finally gathering real steam.
Close to a million doses -- over 951,000, to be more exact -- made their way into the arms of Americans in the past 24 hours, the U.S. Centers for Disease Control and Prevention reported Wednesday. That's the largest number of shots given in one day since the rollout began and a big jump from the previous day, when just under 340,000 doses were given, CBS News reported.
That number is likely to jump quickly after the federal government on Tuesday gave states the OK to vaccinate anyone over 65 and said it would release all the doses of vaccine it has available for distribution. Meanwhile, a number of states have now opened mass vaccination sites in an effort to get larger numbers of people inoculated, CBS News reported."""
summary_text_T5 = summarizer(text, max_length=100, min_length=5, do_sample=False)[0]['summary_text']
print('T5 Model Text Summary: ',summary_text_T5)


tokenizer = T5Tokenizer.from_pretrained("t5-base")
model = T5ForConditionalGeneration.from_pretrained("t5-base")

#human_summary_text = "One month after troubled covid vaccination campaign began, over 951,000 people have been vaccinated so far" # Test Text to check the summarization loss
human_summary_text = "Close to a million doses have been given in the past 24 hours, the cdc says . That's the largest number of shots given in one day since the rollout began."
input_ids = tokenizer(summary_text_T5, return_tensors="pt").input_ids
labels = tokenizer(human_summary_text, return_tensors="pt").input_ids
# the forward function automatically creates the correct decoder_input_ids
loss = model(input_ids=input_ids, labels=labels).loss
loss.item() #Loss calculation
# T5 Model End 


# Define PEGASUS model
model_name = "google/pegasus-xsum"
pegasus_tokenizer = PegasusTokenizer.from_pretrained(model_name)
pegasus_model = PegasusForConditionalGeneration.from_pretrained(model_name)
# Create tokens
tokens = pegasus_tokenizer(text, truncation=True, padding="longest", return_tensors="pt")
# Summarize text
encoded_summary = pegasus_model.generate(**tokens)
# Decode summarized text
decoded_summary = pegasus_tokenizer.decode ( encoded_summary[0],skip_special_tokens=True)
# Define summarization pipeline 
summarizer = pipeline("summarization", model=model_name, tokenizer=pegasus_tokenizer, framework="pt")
summary_text_Pegasus = summarizer(text, max_length=100, min_length=5, do_sample=False)[0]['summary_text']
print('PEGASUS Model Text Summary: ',summary_text_Pegasus)

input_ids = pegasus_tokenizer(summary_text_Pegasus, return_tensors="pt").input_ids
labels = tokenizer(human_summary_text, return_tensors="pt").input_ids
# the forward function automatically creates the correct decoder_input_ids
loss = model(input_ids=input_ids, labels=labels).loss
loss.item() #Loss calculation

# T5 Model End 

#Bart Model
summarizer = pipeline("summarization")
summarizer_bart = summarizer(text, max_length=130, min_length=30, do_sample=False)[0]['summary_text']
print("Bart summarization:",summarizer_bart)

#Bert Sentence Embedding Model

tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
model = BertModel.from_pretrained("bert-base-uncased",output_hidden_states = True)
inputs = tokenizer(text, return_tensors="pt")
outputs = model(**inputs)
hidden_states = outputs.hidden_states
token_vecs = hidden_states[-2][0]
# Calculate the average of all 22 token vectors.
sentence_embedding = torch.mean(token_vecs, dim=0)
print('Bert Summary: ',sentence_embedding)

#model_name ='distilbert-base-uncased'
#distilbert_model = DistilBertModel.from_pretrained('distilbert-base-uncased', output_hidden_states=True)
#distilbert_tokenizer = DistilBertTokenizer.from_pretrained('distilbert-base-uncased')
#summarizer = pipeline("summarization", model=model_name, tokenizer=distilbert_tokenizer, framework="pt")
#summary_text_bert = summarizer(text, max_length=100, min_length=5, do_sample=False)[0]['summary_text']
#print('Distill Bert Summary: ',summary_text_bert)

#ROUGE = Rouge()
#print ("Distill Bert Evaluation")
#ROUGE.get_scores(summary_text_bert, human_summary_text)

ROUGE = Rouge()
print ("Bart Evaluation")
ROUGE.get_scores(summarizer_bart, human_summary_text)

#ROUGE = Rouge()
#print ("T5 Evaluation")
#ROUGE.get_scores(summary_text_T5, human_summary_text)

#ROUGE = Rouge()
#print ("Pegasos Evaluation")
#ROUGE.get_scores(summary_text_Pegasus, human_summary_text)


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Close to a million doses -- over 951,000, to be more exact -- made their way into the arms of Americans in the past 24 hours, the U.S. Centers for Disease Control and Prevention reported Wednesday.
One month after the United States began what has become a troubled rollout of a national COVID vaccination campaign, the effort is finally gathering real steam.

Text Rank:  [(Wednesday, 0.13217188489775455), (real steam, 0.10581605533073346), (CBS News, 0.10101091209671928), (Disease Control, 0.0926596375784235), (mass vaccination sites, 0.09203339500703157), (larger numbers, 0.08517674883908094), (distribution, 0.08479563278004669), (Prevention, 0.07154126745257039), (a national COVID vaccination campaign, 0.06615564564021807), (vaccine, 0.06186683568335749), (states, 0.06079909879910578), (Americans, 0.058530200896772536), (Tuesday, 0.05495515369656152), (people, 0.05490951036967184), (the U

All model checkpoint layers were used when initializing TFT5ForConditionalGeneration.

All the layers of TFT5ForConditionalGeneration were initialized from the model checkpoint at t5-base.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFT5ForConditionalGeneration for predictions without further training.


/usr/local/lib/python3.7/dist-packages/transformers/models/t5/tokenization_t5_fast.py:166: FutureWarning: This tokenizer was incorrectly instantiated with a model max length of 512 which will be corrected in Transformers v5.
For now, this behavior is kept to avoid breaking backwards compatibility when padding/encoding with `truncation is True`.
- Be aware that you SHOULD NOT rely on t5-base automatically truncating your input to 512 when padding/encoding.
- If you want to encode/pad to sequences longer than 512 you can either instantiate this tokenizer with `model_max_length` or pass `max_length` when encoding/padding.
- To avoid this warning, please instantiate this tokenizer with `model_max_length` set to your preferred value.
  FutureWarning,


KeyboardInterrupt: ignored

In [ ]:
#Method 1 Training Algorithm
from transformers import AutoTokenizer
from datasets import load_dataset

base_url = "https://huggingface.co/datasets/lhoestq/demo1/resolve/main/data/"
dataset = load_dataset('csv', data_files={'train': base_url + 'train.csv', 'test': base_url + 'test.csv'})

dataset = load_dataset("yelp_review_full")
dataset["train"][100]

tokenizer = AutoTokenizer.from_pretrained("bert-base-cased")
def tokenize_function(examples):
  return tokenizer(examples["text"], padding="max_length", truncation=True)

tokenized_datasets = dataset.map(tokenize_function, batched=True)
 
small_train_dataset = tokenized_datasets["train"].shuffle(seed=42).select(range(5))
small_eval_dataset = tokenized_datasets["test"].shuffle(seed=42).select(range(5))

print(small_train_dataset)
print(small_eval_dataset)

from transformers import AutoModelForSequenceClassification
model = AutoModelForSequenceClassification.from_pretrained("bert-base-cased", num_labels=5)
 
from transformers import TrainingArguments
training_args = TrainingArguments(output_dir="test_trainer")
 
import numpy as np
from datasets import load_metric
 
metric = load_metric("accuracy")
 
def compute_metrics(eval_pred):
    logits, labels = eval_pred
    predictions = np.argmax(logits, axis=-1)
    return metric.compute(predictions=predictions, references=labels)
 
from transformers import TrainingArguments, Trainer
 
training_args = TrainingArguments(output_dir="test_trainer", evaluation_strategy="epoch")
 
trainer = Trainer(model=model, args=training_args, train_dataset=small_train_dataset,
    eval_dataset=small_eval_dataset,
    compute_metrics=compute_metrics,
)
#trainer.train() # Fine Tuned The Model

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

0 tables [00:00, ? tables/s]

0 tables [00:00, ? tables/s]

Dataset csv downloaded and prepared to /root/.cache/huggingface/datasets/csv/default-79b4e2b51dbc7798/0.0.0/652c3096f041ee27b04d2232d41f10547a8fecda3e284a79a0ec4053c916ef7a. Subsequent calls will reuse this data.


  0%|          | 0/2 [00:00<?, ?it/s]

...

Generating test split:   0%|          | 0/50000 [00:00<?, ? examples/s]

Dataset yelp_review_full downloaded and prepared to /root/.cache/huggingface/datasets/yelp_review_full/yelp_review_full/1.0.0/e8e18e19d7be9e75642fc66b198abadb116f73599ec89a69ba5dd8d1e57ba0bf. Subsequent calls will reuse this data.


  0%|          | 0/2 [00:00<?, ?it/s]

  0%|          | 0/650 [00:00<?, ?ba/s]

KeyboardInterrupt: ignored

In [ ]:
#Method 2 Another Way to Train using Keras API: Convert dataset to tensor flow

from transformers import DefaultDataCollator
from transformers import AutoTokenizer
from datasets import load_dataset
import tensorflow as tf
from transformers import TFAutoModelForSequenceClassification
from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Model
from tensorflow.keras import models
from tensorflow.keras import backend as K
from tensorflow.keras.preprocessing.sequence import pad_sequences
from google.colab import drive
import pandas as pd

drive.mount('/content/drive')
%cd /content/drive/My Drive/Cases/

base_url = "https://huggingface.co/datasets/lhoestq/demo1/resolve/main/data/"
path_to_file = "/content/drive/My Drive/Cases/"

dataset = load_dataset('csv', data_files={'train': base_url + 'train.csv', 'test': base_url + 'test.csv'})
#dataset = load_dataset('csv', data_files={'train': path_to_file + 'CaseSummarizationNew.csv','test': path_to_file + 'CaseSummarizationNewTest.csv'}, encoding="utf-8")

#dataset = load_dataset("billsum", split="ca_test")
#dataset = dataset.train_test_split(test_size=0.2)

#train_data = load_dataset("cnn_dailymail","3.0.0",split="train")
#val_data = load_dataset("cnn_dailymail","3.0.0",split="validation[:10%]")
dataset = load_dataset("yelp_review_full")
#dataset = load_dataset("input_text")
#print("Dataset",dataset["train"][100])
print("Dataset 1",dataset)

tokenizer = AutoTokenizer.from_pretrained("bert-base-cased",num_labels=5)

def count_matches(labels,preds):
  print(labels)
  print(preds)
  return sum ([1 if label ==pred else 0
               for label,pred in zip(labels,preds)
               ]
              )
def tokenize_functionNew(examples):
  return tokenizer(examples["Input_Text"], padding="max_length", truncation=True)

def tokenize_functionOld(examples):
  return tokenizer(examples["text"], padding="max_length", truncation=True)

def tokenize_functionCNN(examples):
  return tokenizer(examples["article"], padding="max_length", truncation=True)

prefix = "summarize: "
def tokenize_functionSummary(examples):
    inputs = [prefix + doc for doc in examples["text"]]
    model_inputs = tokenizer(inputs, max_length=1024, truncation=True)

    with tokenizer.as_target_tokenizer():
        labels = tokenizer(examples["summary"], max_length=128, truncation=True)
    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

print("dataset is:",dataset)
print("dataset is:",dataset.data)

#dataset = load_dataset('csv', data_files={'train': path_to_file + 'CaseSummarization.csv','test': path_to_file + 'CaseSummarizationTest.csv'}, encoding="utf-8")
tokenized_datasets = dataset.map(tokenize_functionOld, batched=True)
small_train_dataset = tokenized_datasets["train"].shuffle(seed=42).select(range(2))
small_eval_dataset = tokenized_datasets["test"].shuffle(seed=42).select(range(2))
#print ("Training Set 2", small_train_dataset)
#print ("Eval Set 2", small_eval_dataset)

print ("Summary", dataset.data)


from transformers import DataCollatorForSeq2Seq

model = TFAutoModelForSequenceClassification.from_pretrained("bert-base-cased",num_labels=5)
data_collator = DefaultDataCollator(return_tensors="tf")
from transformers import AutoModelForSeq2SeqLM, Seq2SeqTrainingArguments, Seq2SeqTrainer

#model = AutoModelForSeq2SeqLM.from_pretrained("t5-small")

#data_collator = DataCollatorForSeq2Seq(tokenizer=tokenizer, model=model, return_tensors="tf")

#print("Example:", small_train_dataset)
#print("Labels:", small_train_dataset["label"])
#tf.squeeze(small_train_dataset["label"])
#tf.squeeze(small_eval_dataset["label"])

tf_train_dataset = small_train_dataset.to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    label_cols=["labels"],
    shuffle=True,
    collate_fn=data_collator,
    batch_size=8,)

tf_validation_dataset =  small_eval_dataset.to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    label_cols=["labels"],
    shuffle=False,
    collate_fn=data_collator,
    batch_size=8,
)

print ("Tensor Set", tf_train_dataset)
print ("Tensor Set", tf_validation_dataset)

train_data = [['Percy Jackson is a protagonist','Percy Jackson is a protagonist']]

train_df = pd.DataFrame(train_data,columns=["input_text","target_text"])

eval_data = [['MB is a protagonist','Percy Jackson is a protagonist']]

eval_df = pd.DataFrame(eval_data,columns=["input_text","target_text"])

tf.convert_to_tensor(train_df["input_text"])
tf.convert_to_tensor(train_df["target_text"])
tf.convert_to_tensor(eval_df["input_text"])
tf.convert_to_tensor(eval_df["target_text"])

model.compile(
    optimizer=tf.keras.optimizers.Adam(learning_rate=5e-5),
    loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
    metrics=tf.metrics.SparseCategoricalAccuracy(),
)
print("TF Train",tf_train_dataset)
print("TF Validation", tf_validation_dataset)

print("Labels = ",tf_train_dataset.element_spec[0])
tf_dict = tf_train_dataset.element_spec[0]
tf_labels = tf_dict['labels']
print("Labels 1 = ",tf_labels)
#tf_labels = tf.squeeze(tf_labels, axis = -1)
print("Labels 2 = ",tf_labels)

#model.fit(train_df,validation_data=eval_df,epochs=3)
#results = model.eval_model(eval_df)
#tf.squeeze(tf_train_dataset,axis=-1)
#tf.squeeze(tf_validation_dataset["labels"],axis=-1)
model.fit(tf_train_dataset, validation_data=tf_validation_dataset, epochs=3)

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
/content/drive/My Drive/Cases


  0%|          | 0/2 [00:00<?, ?it/s]

  0%|          | 0/2 [00:00<?, ?it/s]

Dataset 1 DatasetDict({
    train: Dataset({
        features: ['label', 'text'],
        num_rows: 650000
    })
    test: Dataset({
        features: ['label', 'text'],
        num_rows: 50000
    })
})


dataset is: DatasetDict({
    train: Dataset({
        features: ['label', 'text'],
        num_rows: 650000
    })
    test: Dataset({
        features: ['label', 'text'],
        num_rows: 50000
    })
})
dataset is: {'train': MemoryMappedTable
label: int64
text: string
----
label: [[4,1,3,3,0,4,4,0,1,2,...,1,4,4,2,2,4,3,1,1,0],[1,2,1,0,0,0,0,0,0,4,...,4,1,3,3,3,1,0,3,0,0],[0,0,2,0,0,0,0,0,2,0,...,1,3,3,2,2,1,0,2,3,0],[0,0,0,3,1,2,3,1,3,3,...,1,0,1,2,2,1,4,2,4,0],[0,0,0,2,3,3,2,1,2,3,...,4,1,0,0,0,0,0,0,0,0],[0,0,0,0,0,0,0,0,0,4,...,3,4,3,1,3,3,1,2,1,2],[4,1,2,0,4,3,1,2,0,2,...,4,1,1,0,1,1,0,1,3,2],[4,2,0,2,3,4,0,1,2,1,...,0,0,0,2,1,1,2,3,2,2],[3,2,4,3,3,3,0,4,4,1,...,1,0,1,0,0,0,1,0,0,0],[1,1,1,2,1,0,0,0,0,2,...,2,1,1,1,1,2,1,1,2,1],...[1,2,1,0,0,0,1,2,1,2,...,0,4,4,3,3,1,0,2,3,1],[1,0,0,3,0,4,0,2,2,2,...,4,3,1,2,3,2,1,3,0,4],[3,1,3,3,2,1,0,0,0,4,...,4,2,3,4,0,3,2,3,2,0],[4,2,4,1,1,3,1,4,4,4,...,3,0,0,1,1,3,1,1,0,4],[4,4,0,0,2,0,0,0,0,3,...,2,4,4,4,4,4,4,4,4,4],[2,4,1,0,4,4,4,4,0,0,

All model checkpoint layers were used when initializing TFBertForSequenceClassification.

Some layers of TFBertForSequenceClassification were not initialized from the model checkpoint at bert-base-cased and are newly initialized: ['classifier']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Tensor Set <PrefetchDataset element_spec=({'labels': TensorSpec(shape=(None,), dtype=tf.int64, name=None), 'input_ids': TensorSpec(shape=(None, 512), dtype=tf.int64, name=None), 'attention_mask': TensorSpec(shape=(None, 512), dtype=tf.int64, name=None)}, TensorSpec(shape=(None,), dtype=tf.int64, name=None))>
Tensor Set <PrefetchDataset element_spec=({'labels': TensorSpec(shape=(None,), dtype=tf.int64, name=None), 'input_ids': TensorSpec(shape=(None, 512), dtype=tf.int64, name=None), 'attention_mask': TensorSpec(shape=(None, 512), dtype=tf.int64, name=None)}, TensorSpec(shape=(None,), dtype=tf.int64, name=None))>
TF Train <PrefetchDataset element_spec=({'labels': TensorSpec(shape=(None,), dtype=tf.int64, name=None), 'input_ids': TensorSpec(shape=(None, 512), dtype=tf.int64, name=None), 'attention_mask': TensorSpec(shape=(None, 512), dtype=tf.int64, name=None)}, TensorSpec(shape=(None,), dtype=tf.int64, name=None))>
TF Validation <PrefetchDataset element_spec=({'labels': TensorSpec(shape

In [ ]:
#Method 3 Training using PyTorch

del model
del pytorch_model
del trainer
torch.cuda.empty_cache()

tokenized_datasets = tokenized_datasets.remove_columns(["text"])
tokenized_datasets = tokenized_datasets.rename_column("label", "labels")
tokenized_datasets.set_format("torch")
small_train_dataset = tokenized_datasets["train"].shuffle(seed=42).select(range(1000))
small_eval_dataset = tokenized_datasets["test"].shuffle(seed=42).select(range(1000))
 
from torch.utils.data import DataLoader
 
train_dataloader = DataLoader(small_train_dataset, shuffle=True, batch_size=8)
eval_dataloader = DataLoader(small_eval_dataset, batch_size=8)
 
from transformers import AutoModelForSequenceClassification
 
model = AutoModelForSequenceClassification.from_pretrained("bert-basecased", num_labels=5)
 
from torch.optim import AdamW
 
optimizer = AdamW(model.parameters(), lr=5e-5)
 
from transformers import get_scheduler
 
num_epochs = 3
num_training_steps = num_epochs * len(train_dataloader)
lr_scheduler = get_scheduler(
    name="linear", optimizer=optimizer, num_warmup_steps=0, num_training_steps=num_training_steps
)
 
import torch
 
device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")
model.to(device)
 
from tqdm.auto import tqdm
 
progress_bar = tqdm(range(num_training_steps))
 
model.train()
for epoch in range(num_epochs):
    for batch in train_dataloader:
        batch = {k: v.to(device) for k, v in batch.items()}
        outputs = model(**batch)
        loss = outputs.loss
        loss.backward()
 
        optimizer.step()
        lr_scheduler.step()
        optimizer.zero_grad()
        progress_bar.update(1)
 
metric = load_metric("accuracy")
model.eval()
for batch in eval_dataloader:
    batch = {k: v.to(device) for k, v in batch.items()}
    with torch.no_grad():
        outputs = model(**batch)
 
    logits = outputs.logits
    predictions = torch.argmax(logits, dim=-1)
    metric.add_batch(predictions=predictions, references=batch["labels"])
 
metric.compute()


In [ ]:
!pip install streamlit -q
!pip install bert-extractive-summarizer
from google.colab import drive
drive.mount('/content/drive')
%cd /content/drive/My Drive/Cases/

In [ ]:
!pip install streamlit-option-menu

In [ ]:
%%writefile app.py
import streamlit as st
import os
import pdfplumber
#import PyPDF2
import pathlib
#from transformers import pipeline
import spacy
import torch
import torch.nn as nn
import pytextrank
from transformers import T5Tokenizer, T5ForConditionalGeneration
from transformers import PegasusForConditionalGeneration
from transformers import PegasusTokenizer
from transformers import BertTokenizer, BertModel
from transformers import DistilBertModel, DistilBertTokenizer
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
from rouge import Rouge
from summarizer import Summarizer,TransformerSummarizer
#Tokenizer
from transformers import RobertaTokenizerFast
from transformers import AutoTokenizer,BertConfig, EncoderDecoderConfig, EncoderDecoderModel
from transformers import GPT2Tokenizer, GPT2Model
from streamlit_option_menu import option_menu



#selected = option_menu(
#  menu_title = None,
#  options=["Home", "Summarizer", "About the founder"],
#  orientation = "horizontal",
#  )

st.write('## Natural Language Processor To Generate Summaries of Legal Cases')
st.write('### Input Texts that you want to summarize or choose a file')
textCase = st.text_area('Input case as text here:', height=150)  

path_to_file = "/content/drive/My Drive/Cases/"
file_list = os.listdir(path_to_file)
chooseSelectBox = st.checkbox('Choose Case File')
uploaded_file = st.selectbox("Choose a Case file as pdf", file_list)

#@st.cache  # Added this
#def initSummary():
#  strSummary = ""
#  textSummary = ""
#  caseSummary = ""
#  return strSummary,textSummary,caseSummary

#strSummary,textSummary,caseSummary = initSummary() 


if 'strSummary' not in st.session_state:
    st.session_state.strSummary = ""
if 'textSummary' not in st.session_state:
    st.session_state.textSummary = ""
if 'caseSummary' not in st.session_state:
    st.session_state.caseSummary = ""

if(chooseSelectBox):
  if uploaded_file is not None:
      #uploaded_fileName = uploaded_file.name
      uploaded_fileName = uploaded_file
      uploaded_fileName = path_to_file+uploaded_fileName
      #pdfFileObj = open(uploaded_fileName, 'rb')
      #pdfReader = PyPDF2.PdfFileReader(pdfFileObj)
      #documentPage = []
      #document = []
      #strDataInput = ""
      
      #for page in range(pdfReader.numPages):
      #      pageObj = pdfReader.getPage(page)
      #      strCleanData = pageObj.extractText() 
      #      strDataInput = strDataInput+strCleanData
      #      documentPage.append(strCleanData)
      #document.append(documentPage)
      #pdfFileObj.close()

      document=[]
      iIndex = 0
     
      documentPage = []
      strDataInput = ""
      with pdfplumber.open(uploaded_fileName) as pdf:
          totalpages = len(pdf.pages)
          for i in range(0,totalpages):
            extracted_page = pdf.pages[i]
            extracted_text = extracted_page.extract_text()
            strDataInput = strDataInput+extracted_text
            documentPage.append(extracted_text)
          document.append(documentPage)
          iIndex+=1
      pdf.close()
else:
  strDataInput = textCase


optionAlgo = st.selectbox('Choose the summarization algorithm',('TextRank','Transformer:T5', 'Transformer:Pegasos', 'Transformer:Bert', 'Transformer:Bert2BertCNN','Transformer:Bart','GPT2','XLNET'))
optionTraining = st.selectbox('Training Technique',('Autotokenizer','Keras:TensorFlow', 'Pytorch'))
buttonClicked = st.button('Generate Summary')

#try: strSummary
#except NameError: strSummary = None

#if strSummary is None:
#    strSummary=""
#    textSummary=""
#    caseSummary=""

if (buttonClicked and uploaded_file is not None):

  if (optionAlgo == "TextRank"):
    nlp = spacy.load("en_core_web_lg")
    nlp.add_pipe("textrank")
    doc = nlp(strDataInput)
    for sent in doc._.textrank.summary(limit_phrases=2, limit_sentences=2):
          print(sent)
    Phrases_and_ranks = [(phrase.chunks[0], phrase.rank) for phrase in doc._.phrases]
    st.session_state.strSummary = Phrases_and_ranks[:100]
  elif (optionAlgo == "Transformer:T5"):
    # T5 Model Start - Abstraction Encoding/Decoding
    model_name = "t5-large"
    max_length = 500
    min_length = 50
    # initialize the model architecture and weights
    t5_model = T5ForConditionalGeneration.from_pretrained(model_name)
    # initialize the model tokenizer
    t5_tokenizer = T5Tokenizer.from_pretrained(model_name)

    filename = "/content/drive/My Drive/Cases/T5Model" 
    filenameTok = "/content/drive/My Drive/Cases/T5Model/Tokenizer" 
    from tensorflow import keras
    t5_model = keras.models.load_model(filename,compile=False)
    t5_tokenizer = AutoTokenizer.from_pretrained("/content/drive/My Drive/Cases/T5Model/Tokenizer")

    inputs = t5_tokenizer.encode("summarize:" + strDataInput, return_tensors="pt", max_length=512, 
    padding='max_length', truncation=True)
    summary_ids = t5_model.generate(inputs,num_beams=int(2),no_repeat_ngram_size=3,
          length_penalty=2.0,min_length=min_length,max_length=max_length,early_stopping=True)

    output = t5_tokenizer.decode(summary_ids[0], skip_special_tokens=True, clean_up_tokenization_spaces=True)
    st.session_state.strSummary = output
  elif (optionAlgo == "Transformer:Pegasos"):
    model_name = "google/pegasus-xsum"
    pegasus_tokenizer = PegasusTokenizer.from_pretrained(model_name)
    pegasus_model = PegasusForConditionalGeneration.from_pretrained(model_name)
    # Create tokens
    tokens = pegasus_tokenizer(strDataInput, truncation=True, padding="longest", return_tensors="pt")
    # Summarize text
    encoded_summary = pegasus_model.generate(**tokens)
    # Decode summarized text
    decoded_summary = pegasus_tokenizer.decode ( encoded_summary[0],skip_special_tokens=True)
    st.session_state.strSummary = decoded_summary
  elif(optionAlgo == "Transformer:Bert"):
    max_length = 500
    min_length = 50
    #Bert Sentence Embedding Model
    model_name = "bert-base-uncased"
    bert_tokenizer = BertTokenizer.from_pretrained(model_name)
    bert_model = BertModel.from_pretrained(model_name, output_hidden_states = True ) #output_hidden_states = True
    inputs = bert_tokenizer(strDataInput, return_tensors="pt",max_length=512,padding='max_length', truncation=True)
    outputs = bert_model(**inputs)
    #strSummary = outputs  #hidden_states
    #strSummary = bert_tokenizer.decode(outputs[0])
    model = Summarizer()
    #st.write(model)
    result = model(strDataInput, ratio = 0.1)
    #st.write(result)
    full = ''.join(result)
    st.session_state.strSummary = full
  elif(optionAlgo == "Transformer:Bert2BertCNN"):
    model = EncoderDecoderModel.from_pretrained("patrickvonplaten/bert2bert_cnn_daily_mail")
    tokenizer = AutoTokenizer.from_pretrained("patrickvonplaten/bert2bert_cnn_daily_mail")
    input_ids = tokenizer(strDataInput, return_tensors="pt",max_length=512,padding='max_length', truncation=True).input_ids

    # autoregressively generate summary (uses greedy decoding by default)
    generated_ids = model.generate(input_ids)
    generated_text = tokenizer.batch_decode(generated_ids, skip_special_tokens=True)[0]
    st.session_state.strSummary = generated_text
  elif(optionAlgo == "GPT2"):
    GPT2_model = TransformerSummarizer(transformer_type="GPT2",transformer_model_key="gpt2-medium")
    strResult = ''.join(GPT2_model(strDataInput, min_length=60))
    st.session_state.strSummary = strResult
  elif (optionAlgo == "XLNET"):
    model = TransformerSummarizer(transformer_type="XLNet",transformer_model_key="xlnet-base-cased")
    strResult = ''.join(model(strDataInput, min_length=60))
    st.session_state.strSummary = strResult
  else:
    st.session_state.strSummary = "Model Not Implemented Yet"

textOriginal = st.text_area('Original Text',value = strDataInput, height=150)

if (st.session_state.strSummary !=""):
  st.session_state.textSummary = st.text_area('Text Summary',value = st.session_state.strSummary, height=150) 
  st.session_state.caseSummary = st.text_area('Actual Case Summary',value = st.session_state.strSummary, height=150)
#else:
#  textSummary = st.text_area('Text Summary',value = textSummary, height=150) 
#  caseSummary = st.text_area('Actual Case Summary',value = caseSummary, height=150)
  
rougeClicked = st.button('Generate Rouge Score')

if(rougeClicked):
  if(st.session_state.textSummary != "" and st.session_state.caseSummary != ""):
    rougeObj = Rouge()
    scoreObj = rougeObj.get_scores(st.session_state.textSummary, st.session_state.caseSummary)
    score = st.text_area('Rouge Score',value = scoreObj, height=100)





  




In [ ]:
! pip install pyngrok

In [ ]:
from pyngrok import ngrok

In [ ]:
ngrok.set_auth_token("2DFRrpyp9EziRs4rpG0wFv79OHg_6NxD8Daqfvu5cZXAmrv9J") 

In [ ]:
!nohup streamlit run app.py --server.port 80 &
url = ngrok.connect(port = '80')
print(url)

In [ ]:
!pip install rouge

In [ ]:
from pyngrok import ngrok

tunnels=ngrok.get_tunnels()
tunnels


# try:
#     # Block until CTRL-C or some other terminating event
#     ngrok_process.proc.wait()
# except KeyboardInterrupt:
#     print(" Shutting down server.")

#     ngrok.kill()

In [ ]:
import os
import PyPDF2
import pathlib
from transformers import pipeline
import spacy
import torch
import torch.nn as nn
import pytextrank
from transformers import T5Tokenizer, T5ForConditionalGeneration
from transformers import PegasusForConditionalGeneration
from transformers import PegasusTokenizer
from transformers import BertTokenizer, BertModel,TFBertModel
from transformers import DistilBertModel, DistilBertTokenizer
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
from rouge import Rouge
from google.colab import drive
from summarizer import Summarizer

drive.mount('/content/drive')
%cd /content/drive/My Drive/Cases/

path_to_file = "SupremeCourtCase1.PDF"
#file_list = os.listdir(path_to_file)
#uploaded_file = st.selectbox("Or Choose a Case file as pdf", file_list)
uploaded_file=path_to_file
if uploaded_file is not None:
    #uploaded_fileName = uploaded_file.name
    uploaded_fileName = "SupremeCourtCase1.PDF"
    #uploaded_fileName = path_to_file+uploaded_fileName
    print(uploaded_fileName)
    pdfFileObj = open(uploaded_fileName, 'rb')
    pdfReader = PyPDF2.PdfFileReader(pdfFileObj)
    documentPage = []
    document = []
    strDataInput = ""
    for page in range(pdfReader.numPages):
          pageObj = pdfReader.getPage(page)
          strCleanData = pageObj.extractText() 
          strDataInput = strDataInput+strCleanData
          documentPage.append(strCleanData)
    document.append(documentPage)
    pdfFileObj.close()
max_length = 500
min_length = 50
#Bert Sentence Embedding Model
model_name = "bert-base-uncased"
bert_tokenizer = BertTokenizer.from_pretrained(model_name)
bert_model = BertModel.from_pretrained(model_name, output_hidden_states = True ) #output_hidden_states = True
inputs = bert_tokenizer(strDataInput, return_tensors="pt",max_length=512,padding='max_length', truncation=True)
#inputs = bert_tokenizer.encode("summarize:" + strDataInput, return_tensors="pt", max_length=512, 
#  padding='max_length', truncation=True)

outputs = bert_model(**inputs)
#summary_ids = bert_model.generate(inputs,num_beams=int(2),no_repeat_ngram_size=3,length_penalty=2.0,
#  min_length=min_length,max_length=max_length,early_stopping=True)
#output = bert_tokenizer.decode(summary_ids[0], skip_special_tokens=True, clean_up_tokenization_spaces=True)
#logits = outputs.logits

hidden_states = outputs.hidden_states
token_vecs = hidden_states[-2][0]
print(token_vecs)
#token_vecs = hidden_states[-2][0]
# Calculate the average of all 22 token vectors.
sentence_embedding = torch.mean(token_vecs, dim=0)
print(sentence_embedding)

for i,word in enumerate(sentence_embedding):
  print("The encoding for ",i+1,"th word is : \n\n",word)

model = Summarizer()
result = model(strDataInput, min_length=50,max_length = 500)
strSummary = result
print("Summary is:",strSummary)
#start_logits = layers.Dense(1, name="start_logit", use_bias=False)(sentence_embedding)
#start_logits = layers.Flatten()(start_logits)

#end_logits = layers.Dense(1, name="end_logit", use_bias=False)(sentence_embedding)
#end_logits = layers.Flatten()(end_logits)

#start_probs = layers.Activation(keras.activations.softmax)(start_logits)
#end_probs = layers.Activation(keras.activations.softmax)(end_logits)

#model = keras.Model(
#    inputs=[input_ids, token_type_ids, attention_mask],
#    outputs=[start_probs, end_probs],
#)



In [ ]:
from transformers import DefaultDataCollator
from transformers import AutoTokenizer
from datasets import load_dataset
import tensorflow as tf
from transformers import TFAutoModelForSequenceClassification
from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Model
from tensorflow.keras import models
from tensorflow.keras import backend as K
from tensorflow.keras.preprocessing.sequence import pad_sequences
from google.colab import drive
import pandas as pd
from transformers import TFAutoModelForSeq2SeqLM

from datasets import load_dataset

billsum = load_dataset("billsum", split="ca_test")
billsum = billsum.train_test_split(test_size=0.2)

from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("t5-small")
prefix = "summarize: "


def preprocess_function(examples):
    inputs = [prefix + doc for doc in examples["text"]]
    model_inputs = tokenizer(inputs, max_length=1024, truncation=True)

    with tokenizer.as_target_tokenizer():
        labels = tokenizer(examples["summary"], max_length=128, truncation=True)

    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

tokenized_billsum = billsum.map(preprocess_function, batched=True)

from transformers import DataCollatorForSeq2Seq

#data_collator = DataCollatorForSeq2Seq(tokenizer=tokenizer, model=model)

from transformers import DataCollatorForSeq2Seq
model = TFAutoModelForSeq2SeqLM.from_pretrained("t5-small")
data_collator = DataCollatorForSeq2Seq(tokenizer=tokenizer, model=model, return_tensors="tf")
from transformers import AutoModelForSeq2SeqLM, Seq2SeqTrainingArguments, Seq2SeqTrainer


from transformers import DataCollatorForSeq2Seq

from transformers import AutoModelForSeq2SeqLM, Seq2SeqTrainingArguments, Seq2SeqTrainer

model = AutoModelForSeq2SeqLM.from_pretrained("t5-small")

data_collator = DataCollatorForSeq2Seq(tokenizer=tokenizer, model=model, return_tensors="tf")

small_train_dataset = tokenized_billsum["train"].shuffle(seed=42).select(range(2))
small_eval_dataset = tokenized_billsum["test"].shuffle(seed=42).select(range(2))

#training_args = Seq2SeqTrainingArguments(
#    output_dir="./results",
#    evaluation_strategy="epoch",
#    learning_rate=2e-5,
#    per_device_train_batch_size=16,
#    per_device_eval_batch_size=16,
#    weight_decay=0.01,
#    save_total_limit=3,
#    num_train_epochs=1,
#    fp16=False,
#)

#trainer = Seq2SeqTrainer(
#    model=model,
#    args=training_args,
#    train_dataset= small_train_dataset, #tokenized_billsum["train"],
#    eval_dataset= small_eval_dataset, #tokenized_billsum["test"],
#    tokenizer=tokenizer,
#    data_collator=data_collator,
#)

#trainer.train()
#data_collator = DefaultDataCollator(return_tensors="tf")

tf_train_set = tokenized_billsum["train"].to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    shuffle=True,
    batch_size=16,
    collate_fn=data_collator,
)

tf_test_set = small_eval_dataset.to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    label_cols=["labels"],
    shuffle=False,
    batch_size=16,
    collate_fn=data_collator,
)

from transformers import create_optimizer, AdamWeightDecay

optimizer = AdamWeightDecay(learning_rate=2e-5, weight_decay_rate=0.01)

from transformers import TFAutoModelForSeq2SeqLM

model = TFAutoModelForSeq2SeqLM.from_pretrained("t5-small")
model.fit(x=tf_train_set, validation_data=tf_test_set, epochs=3) 

Could not locate the tokenizer configuration file, will try to use the model config instead.
loading configuration file https://huggingface.co/t5-small/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/fe501e8fd6425b8ec93df37767fcce78ce626e34cc5edc859c662350cf712e41.406701565c0afd9899544c1cb8b93185a76f00b31e5ce7f6e18bbaef02241985
Model config T5Config {
  "_name_or_path": "t5-small",
  "architectures": [
    "T5WithLMHeadModel"
  ],
  "d_ff": 2048,
  "d_kv": 64,
  "d_model": 512,
  "decoder_start_token_id": 0,
  "dense_act_fn": "relu",
  "dropout_rate": 0.1,
  "eos_token_id": 1,
  "feed_forward_proj": "relu",
  "initializer_factor": 1.0,
  "is_encoder_decoder": true,
  "is_gated_act": false,
  "layer_norm_epsilon": 1e-06,
  "model_type": "t5",
  "n_positions": 512,
  "num_decoder_layers": 6,
  "num_heads": 8,
  "num_layers": 6,
  "output_past": true,
  "pad_token_id": 0,
  "relative_attention_max_distance": 128,
  "relative_attention_num_buckets": 32,
  "task

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

loading configuration file https://huggingface.co/t5-small/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/fe501e8fd6425b8ec93df37767fcce78ce626e34cc5edc859c662350cf712e41.406701565c0afd9899544c1cb8b93185a76f00b31e5ce7f6e18bbaef02241985
Model config T5Config {
  "_name_or_path": "t5-small",
  "architectures": [
    "T5WithLMHeadModel"
  ],
  "d_ff": 2048,
  "d_kv": 64,
  "d_model": 512,
  "decoder_start_token_id": 0,
  "dense_act_fn": "relu",
  "dropout_rate": 0.1,
  "eos_token_id": 1,
  "feed_forward_proj": "relu",
  "initializer_factor": 1.0,
  "is_encoder_decoder": true,
  "is_gated_act": false,
  "layer_norm_epsilon": 1e-06,
  "model_type": "t5",
  "n_positions": 512,
  "num_decoder_layers": 6,
  "num_heads": 8,
  "num_layers": 6,
  "output_past": true,
  "pad_token_id": 0,
  "relative_attention_max_distance": 128,
  "relative_attention_num_buckets": 32,
  "task_specific_params": {
    "summarization": {
      "early_stopping": true,
      "length_penal

AttributeError: ignored

In [ ]:

encoded = bert_tokenizer.encode(strDataInput)
# encoded: [101, 2070, 3793, 102]
decoded = bert_tokenizer.decode(encoded)
# decoded: [CLS] some text [SEP]
strSummary = decoded  #hidden_states
#strSummary = logits

encoder = TFBertModel.from_pretrained(model_name)

## QA Model
input_ids = layers.Input(shape=(max_length,), dtype=tf.int32)
token_type_ids = layers.Input(shape=(max_length,), dtype=tf.int32)
attention_mask = layers.Input(shape=(max_length,), dtype=tf.int32)
embedding = encoder(
    input_ids, token_type_ids=token_type_ids, attention_mask=attention_mask
)[0]

start_logits = layers.Dense(1, name="start_logit", use_bias=False)(embedding)
start_logits = layers.Flatten()(start_logits)

end_logits = layers.Dense(1, name="end_logit", use_bias=False)(embedding)
end_logits = layers.Flatten()(end_logits)

start_probs = layers.Activation(keras.activations.softmax)(start_logits)
end_probs = layers.Activation(keras.activations.softmax)(end_logits)

model = keras.Model(
    inputs=[input_ids, token_type_ids, attention_mask],
    outputs=[start_probs, end_probs],
)
loss = keras.losses.SparseCategoricalCrossentropy(from_logits=False)
optimizer = keras.optimizers.Adam(lr=5e-5)
model.compile(optimizer=optimizer, loss=[loss, loss])
strSummary = model.summary()
print("Summary:",strSummary)




#Roberta 

    tokenizer = RobertaTokenizerFast.from_pretrained("roberta-base")
    tokenizer.bos_token = tokenizer.cls_token
    tokenizer.eos_token = tokenizer.sep_token
    #parameter setting
    batch_size=256  #
    encoder_max_length=100
    decoder_max_length=8
    config_encoder = BertConfig()
    config_decoder = BertConfig()
    config = EncoderDecoderConfig.from_encoder_decoder_configs(config_encoder, config_decoder)
    model = EncoderDecoderModel(config=config)
    #model = EncoderDecoderModel.from_pretrained("roberta-base", "roberta-base")
    model.to("cuda")
    batch_size = 1024
    model.config.decoder_start_token_id = tokenizer.bos_token_id                                             
    model.config.eos_token_id = tokenizer.eos_token_id

    # sensible parameters for beam search
    # set decoding params                               
    model.config.max_length = 100
    model.config.early_stopping = True
    model.config.no_repeat_ngram_size = 3
    model.config.length_penalty = 2.0
    model.config.num_beams = 4
    model.config.vocab_size = model.config.encoder.vocab_size
    # map data correctly
    def generate_summary(batch):
        # Tokenizer will automatically set [BOS] <text> [EOS]
        inputs = tokenizer(batch["Text"], padding="max_length", truncation=True, max_length=100, return_tensors="pt")
        input_ids = inputs.input_ids.to("cuda")
        attention_mask = inputs.attention_mask.to("cuda")
        outputs = model.generate(input_ids, attention_mask=attention_mask)
        # all special tokens including will be removed
        output_str = tokenizer.batch_decode(outputs, skip_special_tokens=True)
        batch["pred"] = output_str
        return batch
    results = test_data.map(generate_summary, batched=True, batch_size=batch_size, remove_columns=["Text"])
    pred_str = results["pred"]
    strSummary = results["Summary"]

In [ ]:
#T5 Training 
from transformers import DefaultDataCollator
from transformers import AutoTokenizer
from datasets import load_dataset
import tensorflow as tf
from transformers import TFAutoModelForSequenceClassification
from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Model
from tensorflow.keras import models
from tensorflow.keras import backend as K
from tensorflow.keras.preprocessing.sequence import pad_sequences
from google.colab import drive
import pandas as pd
from transformers import TFAutoModelForSeq2SeqLM

from datasets import load_dataset
billsum = load_dataset("billsum", split="ca_test")
billsum = billsum.train_test_split(test_size=0.2)
billsum["train"][0]
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("t5-small")
prefix = "summarize: "

def preprocess_function(examples):
    inputs = [prefix + doc for doc in examples["text"]]
    model_inputs = tokenizer(inputs, max_length=1024, truncation=True)

    with tokenizer.as_target_tokenizer():
        labels = tokenizer(examples["summary"], max_length=128, truncation=True)

    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

tokenized_billsum = billsum.map(preprocess_function, batched=True)

from transformers import DataCollatorForSeq2Seq
model = TFAutoModelForSeq2SeqLM.from_pretrained("t5-small")
data_collator = DataCollatorForSeq2Seq(tokenizer=tokenizer, model=model, return_tensors="tf")

small_train_dataset = tokenized_billsum["train"].shuffle(seed=42).select(range(5))
small_eval_dataset = tokenized_billsum["test"].shuffle(seed=42).select(range(5))


tf_train_set = small_train_dataset.to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    shuffle=True,
    batch_size=16,
    collate_fn=data_collator,
)

tf_test_set = small_eval_dataset.to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    shuffle=False,
    batch_size=16,
    collate_fn=data_collator,
)

from transformers import create_optimizer, AdamWeightDecay

optimizer = AdamWeightDecay(learning_rate=2e-5, weight_decay_rate=0.01)
from transformers import TFAutoModelForSeq2SeqLM


model.compile(optimizer=optimizer)
model.fit(x=tf_train_set, validation_data=tf_test_set, epochs=10)


Generating train split:   0%|          | 0/18949 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/3269 [00:00<?, ? examples/s]

Generating ca_test split:   0%|          | 0/1237 [00:00<?, ? examples/s]

Dataset billsum downloaded and prepared to /root/.cache/huggingface/datasets/billsum/default/3.0.0/d1e95173aed3acb71327864be74ead49b578522e4c7206048b2f2e5351b57959. Subsequent calls will reuse this data.


/usr/local/lib/python3.7/dist-packages/transformers/models/t5/tokenization_t5_fast.py:166: FutureWarning: This tokenizer was incorrectly instantiated with a model max length of 512 which will be corrected in Transformers v5.
For now, this behavior is kept to avoid breaking backwards compatibility when padding/encoding with `truncation is True`.
- Be aware that you SHOULD NOT rely on t5-small automatically truncating your input to 512 when padding/encoding.
- If you want to encode/pad to sequences longer than 512 you can either instantiate this tokenizer with `model_max_length` or pass `max_length` when encoding/padding.
- To avoid this warning, please instantiate this tokenizer with `model_max_length` set to your preferred value.
  FutureWarning,


  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

All model checkpoint layers were used when initializing TFT5ForConditionalGeneration.

All the layers of TFT5ForConditionalGeneration were initialized from the model checkpoint at t5-small.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFT5ForConditionalGeneration for predictions without further training.
No loss specified in compile() - the model's internal loss computation will be used as the loss. Don't panic - this is a common way to train TensorFlow models in Transformers! To disable this behaviour please pass a loss argument, or explicitly pass `loss=None` if you do not want your model to compute a loss.


Epoch 1/10
1/1 [==============================] - 83s 83s/step - loss: 4.9536 - val_loss: 4.8947
Epoch 2/10
1/1 [==============================] - 41s 41s/step - loss: 4.8972 - val_loss: 4.8216
Epoch 3/10
1/1 [==============================] - 51s 51s/step - loss: 4.7482 - val_loss: 4.7498
Epoch 4/10
1/1 [==============================] - 74s 74s/step - loss: 4.8309 - val_loss: 4.6799
Epoch 5/10
1/1 [==============================] - 48s 48s/step - loss: 4.5995 - val_loss: 4.6109
Epoch 6/10
1/1 [==============================] - 41s 41s/step - loss: 4.6405 - val_loss: 4.5395
Epoch 7/10
1/1 [==============================] - 40s 40s/step - loss: 4.5003 - val_loss: 4.4675
Epoch 8/10
1/1 [==============================] - 41s 41s/step - loss: 4.3707 - val_loss: 4.3993
Epoch 9/10
1/1 [==============================] - 41s 41s/step - loss: 4.4322 - val_loss: 4.3355
Epoch 10/10
1/1 [==============================] - 40s 40s/step - loss: 4.0204 - val_loss: 4.2745


In [ ]:
! pip install huggingface_hub
from transformers import AutoTokenizer
from huggingface_hub import notebook_login

notebook_login()


Login successful
Your token has been saved to /root/.huggingface/token
Authenticated through git-credential store but this isn't the helper defined on your machine.
You might have to re-authenticate when pushing to the Hugging Face Hub. Run the following command in your terminal in case you want to set this credential helper as the default

git config --global credential.helper store


In [ ]:
# You can of course substitute your own username and model here if you've trained and uploaded it!
model_name = "Amanb2004/t5-small-finetuned-xsum"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = TFAutoModelForSeq2SeqLM.from_pretrained(model_name)

OSError: ignored

In [ ]:
from transformers import AutoTokenizer

#T5 Training on Billsum database
from transformers import DefaultDataCollator
from transformers import AutoTokenizer
from datasets import load_dataset
import tensorflow as tf
from transformers import TFAutoModelForSequenceClassification
from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Model
from tensorflow.keras import models
from tensorflow.keras import backend as K
from tensorflow.keras.preprocessing.sequence import pad_sequences
from google.colab import drive
import pandas as pd
from transformers import TFAutoModelForSeq2SeqLM
from transformers import T5Tokenizer, T5ForConditionalGeneration
from transformers import PegasusForConditionalGeneration


from datasets import load_dataset
billsum = load_dataset("billsum", split="ca_test")
billsum = billsum.train_test_split(test_size=0.2)
billsum["train"][0]
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("t5-small")
prefix = "summarize: "

def preprocess_function(examples):
    inputs = [prefix + doc for doc in examples["text"]]
    model_inputs = tokenizer(inputs, max_length=1024, truncation=True)

    with tokenizer.as_target_tokenizer():
        labels = tokenizer(examples["summary"], max_length=128, truncation=True)

    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

tokenized_billsum = billsum.map(preprocess_function, batched=True)

from transformers import DataCollatorForSeq2Seq
model = TFAutoModelForSeq2SeqLM.from_pretrained("t5-small")
data_collator = DataCollatorForSeq2Seq(tokenizer=tokenizer, model=model, return_tensors="tf")

small_train_dataset = tokenized_billsum["train"].shuffle(seed=42).select(range(5))
small_eval_dataset = tokenized_billsum["test"].shuffle(seed=42).select(range(5))


tf_train_set = small_train_dataset.to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    shuffle=True,
    batch_size=16,
    collate_fn=data_collator,
)

tf_test_set = small_eval_dataset.to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    shuffle=False,
    batch_size=16,
    collate_fn=data_collator,
)

from transformers import create_optimizer, AdamWeightDecay

optimizer = AdamWeightDecay(learning_rate=2e-5, weight_decay_rate=0.01)
from transformers import TFAutoModelForSeq2SeqLM


model.compile(optimizer=optimizer)
#model.fit(x=tf_train_set, validation_data=tf_test_set, epochs=10)

filename = "/content/drive/My Drive/Cases/T5Model" 
#filenameTok = "/content/drive/My Drive/Cases/T5Model/Tokenizer" 
#model.save(filename)
#tokenizer.save_pretrained(filenameTok)
from tensorflow import keras
#t5_model = keras.models.load_model(filename,compile=False)
strDataInput = "Hi My name is AB I am Managing Director of PrepSaurus"
#
t5_model = model
t5_tokenizer = tokenizer
max_length = 500
min_length = 50

t5_model = keras.models.load_model(filename,compile=False)
#t5_model = T5ForConditionalGeneration.from_pretrained("/content/drive/My Drive/Cases/T5Model")
# initialize the model tokenizer
#t5_tokenizer = T5Tokenizer.from_pretrained("/content/drive/My Drive/Cases/T5Model/Tokenizer")

t5_tokenizer = AutoTokenizer.from_pretrained("/content/drive/My Drive/Cases/T5Model/Tokenizer")
inputs = t5_tokenizer.encode("summarize:" + strDataInput, return_tensors="pt", max_length=512, 
padding='max_length', truncation=True)
print("T5 Model = ",t5_model)
summary_ids = t5_model.generate(inputs,num_beams=int(2),no_repeat_ngram_size=3,
      length_penalty=2.0,min_length=min_length,max_length=max_length,early_stopping=True)

output = t5_tokenizer.decode(summary_ids[0], skip_special_tokens=True, clean_up_tokenization_spaces=True)
strSummary=output
print("Summary:",strSummary)


  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

All model checkpoint layers were used when initializing TFT5ForConditionalGeneration.

All the layers of TFT5ForConditionalGeneration were initialized from the model checkpoint at t5-small.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFT5ForConditionalGeneration for predictions without further training.
No loss specified in compile() - the model's internal loss computation will be used as the loss. Don't panic - this is a common way to train TensorFlow models in Transformers! To disable this behaviour please pass a loss argument, or explicitly pass `loss=None` if you do not want your model to compute a loss.


T5 Model =  <keras.saving.saved_model.load.TFT5ForConditionalGeneration object at 0x7f0c5eb551d0>


AttributeError: ignored

In [ ]:
#Bert Training on Billsum database
from transformers import DefaultDataCollator
from transformers import AutoTokenizer
from datasets import load_dataset
import tensorflow as tf
from transformers import TFAutoModelForSequenceClassification
from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Model
from tensorflow.keras import models
from tensorflow.keras import backend as K
from tensorflow.keras.preprocessing.sequence import pad_sequences
from google.colab import drive
import pandas as pd
from transformers import TFAutoModelForSeq2SeqLM

from datasets import load_dataset
billsum = load_dataset("billsum", split="ca_test")
billsum = billsum.train_test_split(test_size=0.2)
billsum["train"][0]
from transformers import AutoTokenizer
#tokenizer = AutoTokenizer.from_pretrained("bert-base-cased")
tokenizer = AutoTokenizer.from_pretrained("bert-base-cased",num_labels = 5)

model = TFAutoModelForSequenceClassification.from_pretrained("bert-base-cased",num_labels = 5)

prefix = "summarize: "

def preprocess_function(examples):
    inputs = [prefix + doc for doc in examples["text"]]
    model_inputs = tokenizer(inputs, max_length=1024, truncation=True)

    with tokenizer.as_target_tokenizer():
        labels = tokenizer(examples["summary"], max_length=128, truncation=True)

    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

tokenized_billsum = billsum.map(preprocess_function, batched=True)

from transformers import DataCollatorForSeq2Seq
data_collator = DefaultDataCollator(return_tensors="tf")

small_train_dataset = tokenized_billsum["train"].shuffle(seed=42).select(range(5))
small_eval_dataset = tokenized_billsum["test"].shuffle(seed=42).select(range(5))

tf_train_set = small_train_dataset.to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    shuffle=True,
    batch_size=16,
    collate_fn=data_collator,
)

tf_test_set = small_eval_dataset.to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    shuffle=False,
    batch_size=16,
    collate_fn=data_collator,
)

#from transformers import create_optimizer, AdamWeightDecay

#optimizer = AdamWeightDecay(learning_rate=2e-5, weight_decay_rate=0.01)
#from transformers import TFAutoModelForSeq2SeqLM

model.compile(
    optimizer=tf.keras.optimizers.Adam(learning_rate=5e-5),
    loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
    metrics=tf.metrics.SparseCategoricalAccuracy(),
)

#model.compile(optimizer=optimizer)
model.fit(x=tf_train_set, validation_data=tf_test_set, epochs=10)

All model checkpoint layers were used when initializing TFBertForSequenceClassification.

Some layers of TFBertForSequenceClassification were not initialized from the model checkpoint at bert-base-cased and are newly initialized: ['classifier']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

Epoch 1/10


ValueError: ignored

In [ ]:
import pandas as pd
from matplotlib import pyplot as plt
Rouge1 = [0.16846152,0.155608998, 0.338957761, 0.166875619, 0.341073535, 0.313205803]
Rouge2 = [0.037922024, 0.078433474, 0.199544442, 0.063976105, 0.180217999, 0.156838279]
bins = ['T5','Pegasos','Bert','Bert2BertCNN','GPT2', 'XLNET']
plt.hist(Rouge1, bins = 5)
plt.title('Histogram showing the ROUGE-1 f1 scores of different models')
plt.xlabel('Model')
plt.ylabel('Average ROUGE-1 F1 score')
plt.show()

ImportError: ignored

<Figure size 432x288 with 1 Axes>